In [1]:
import logging
import pyspark
import subprocess
import click
import traceback
from pyspark.sql.types import *
from pyspark.sql import SQLContext
from pyspark.sql.functions import *
from pyspark import SparkConf, SparkContext

def _get_spark_handle():

    _spark = pyspark.sql.SparkSession.builder \
            .master("local[%d]" % 2) \
            .appName(
            "Spark Preprocessing") \
            .config("spark.executor.memory", "4g") \
            .config("spark.sql.execution.arrow.enable", "true") \
            .config("spark.ui.showConsoleProgress", "true") \
            .getOrCreate()

    return _spark


def _spark_handle():
    spark_handle = _get_spark_handle()
    return spark_handle


def _read_file(path):
    df = _spark_handle().read.options().json(path)
    return df


In [11]:
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk

def index_articles(es_endpoint, index_name, articles, count):

    es = Elasticsearch(hosts=[es_endpoint], timeout=5000)
    
    index_count = 0
    ACTIONS = []
    
    for i in articles:
        print i.title
        action = {
            "_index": index_name,
            "_type": "article",
            "_source": {
                "url": i.original_url,
                "title": i.title,
                "words": i.terms,
                "traffic": i.traffic
            }
        }
        ACTIONS.append(action)
        if (index_count > 0 and index_count % 10000 == 0):
            print "Indexing " + str(len(ACTIONS)) + "documents, index_count: " + str(index_count)
            try:
                success, _ = bulk(es, ACTIONS, index = index_name, raise_on_error = False)
            except BulkIndexError:
                print("Oops! " +index_name  +" Failed! Try again...")
            
            count += success
            ACTIONS = []
    index_count += 1
    success, _ = bulk(es, ACTIONS, index = index_name, raise_on_error=False)
    count += success
    print("insert %s lines" % count)
    return count

#index_articles("127.0.0.1:9200", "topic_disco", articles)

In [12]:
import os

directory = '/Users/allen.wu/deep_learning/StepContent__nocontent_title_desc'
count=0
for filename in os.listdir(directory):
    df = _read_file(os.path.join(directory, filename))
    articles = df.select("original_url", "title", "terms", "traffic").collect()
    count = index_articles("127.0.0.1:9200", "topic_disco", articles, count)

 Así se escuchó la tierra durante el sismo del 19S
 Atentan contra Nicolás Maduro; acusan a oposición
 Calendario escolar 2018 - 2019: ¿cuándo caen los días feriados?
 Volkswagen bombardea el cielo de Puebla: deja sin lluvias ni cosecha a campesinos
"13 Reasons Why" premiere party canceled after school shooting
"2001: A Space Odyssey" returns to theatres in 70mm
"48 Hours" Live to Tell: I Remember Everything
"48 Hours" Special: All-American Murder: The Rise and Fall of Aaron Hernandez
"48 Hours: NCIS": A Date with Evil
"A Slow Slipping Away"-- Kris Kristofferson's Long-Undiagnosed Battle with Lyme Disease
"A Valuable LDS Resource for Learning from the Apocrypha," etc.“A Valuable LDS Resource for Learning from the Apocrypha,” etc.
"A place in crisis": Author documents life on disappearing Tangier Island
"Absolutely" a blue Muslim wave coming, says Michigan congressional candidate Rashida Tlaib
"All eyes" on Trump: U.N. to meet amid tension with U.S.
"All my stuff is gone": North Carolin

'Bringing Up Bates' couple seeks fertility answers from Knoxville doctor
'Bringing Up Bates' episode features pregnancy reveal, wedding dress shopping
'Bringing Up Bates' stars Erin Paine, Alyssa Webster deliver babies 2 days apart
'Bringing Up Bates': Gil Bates cries at Josie Bates, Kelton Balka's pending engagement
'Bringing Up Bates:' Big changes coming for Josie Bates, Tori and Bobby Smith
'Bringing Up Bates:' Carlin Bates reveals future plans with boyfriend Evan Stewart
'Broadway Joe' chronicles the N.Y. Jets before they were the Jets
'Broccoli coffee' is the new health trend we didn't ask for
'Brown Bag Bandit' Hits 12th Bank, Deputies Say
'Buckle Up': Michael Avenatti Tweets That Kavanaugh Accuser 'Is Not Alone', Warns Accused Accomplice Mark Judge
'Bucs Beach' opens at Raymond James Stadium
'Buffy the Vampire Slayer' returns in fan-made animated trailer
'Bull market climbs a wall of worry' as many Americans sit on the sidelines
'Bull' star Michael Weatherly reflects on Les Moon

'Unprofessional and distasteful': Details of Baltimore Symphony's sexual harassment investigation test its image
'Unrealistic' Bedtime Rules Shared By Elementary School Go Viral
'Unspecified device' found after report of explosion
'Urban Light': Everything you didn't know about L.A.'s beloved landmark
'Vagina Mohawks' Made An Appearance At New York Fashion Week
'Vampire Diaies': Elena Learns She's Sired To Damon
'Vampire Diaries' Casts Its First Gay Lead Character
'Veep' Final Season to Air in Spring 2019 | Entertainment Tonight
'Vejigantes' Offers A Taste Of Spanish-language Theater
'Venom' is rated PG-13 because Sony reportedly wants Spider-Man and Venom to 'face off' in the future
'Veronica Mars' Revival Ordered to Series at Hulu
'Veronica Mars' is coming back with new episodes on Hulu in 2019
'Veronica' Mars' Revival at Hulu Is Officially a Go
'Very Abnormal Behaviour' From Russian Satellite Sparks Fears It May Be a Space Weapon
'Very Tragic': Girl, 8, Among 5 Shot During Memorial 

10 causes of the Titanic tragedy
10 cemeteries you'll never regret visiting
10 cheap, quirky bars in the DC area
10 cheapest cars: Why (almost) nobody buys them
10 chef secrets: What happens to uneaten bread, what not to order and more
10 claves sobre las leyes y el debate que genera el aborto en México
10 college majors with the best job prospects 
10 common math questions from the SATs that everyone gets wrong
10 computadoras personales que marcaron las últimas tres décadas
10 cookies from around the world that you'll want to try immediately
10 core exercises that are more effective than crunches
10 cosas que debes saber de Beatriz Gutiérrez Müller, la nueva primera dama
10 cosas que tienes que saber sobre 'Locamente millonarios'
10 countries where it's nearly impossible to become a dual citizen
10 crazy Jimmy Butler trades, according to Trade Machine
10 credit score myths and the truths behind them
10 creepy movie dolls you really don't want in your house (including Annabelle), rank

13 Roku tricks you should try right now
13 Rules For Using Commas Without Looking Like An Idiot
13 Scary Movies That Made Us Afraid to Go in the Water | Reader's Digest
13 Schools Where It's Almost Impossible To Fail
13 Secrets Ancestry Trackers Know About Your Family Tree (That You Don’t)
13 Secrets Your Eye Doctor Won't Tell You | Reader's Digest
13 Signs You May Need Marriage Counseling
13 Signs You're In A Dead-End Relationship
13 Signs Your Partner Is Cheating On You
13 Signs of Cancer Men Are Likely to Ignore | Reader's Digest
13 Silent Signs of a Thyroid Problem | Reader's Digest
13 Simple Tricks To A Long And Happy Marriage
13 Songs to Get Witchy to on Halloween
13 Stephen Hawking Quotes That Perfectly Sum Up His Humour And His Brilliance
13 Steps to Recover From Betrayal
13 Strange Superstitions About Death
13 Stunning Images Of The Hindu Festival Of Ram Navami (PICTURES)
13 Subtle Ways Women Are Treated Differently At Work
13 Suicide Warning Signs That Are Easy to Miss | Read

...

Southern Miss coach Jay Hopson discusses Auburn ahead of Saturday’s game
Southern Oregon wildfires: Klondike Fire grows to 55,000 acres
Southern Shrimp and Grits
Southern Spoonbread A Simple, Versatile Dish
Southern Sweet Potato Pie
Southern University fires popular band director, he says he is disappointed with decision
Southern University opens its 10th annual Homecoming Art Exhibition on Sept. 25
Southern quarterback John Lampley comes to life as Jaguars rally past Alabama A&M
Southern restaurant The Larder + The Delta to reopen in Phoenix in March
Southern still finding its way one game into SWAC schedule
Southern stops Alabama A&M 2-point try, edges Bulldogs 29-27 in Mobile
Southern to play Alabama A&M in the inaugural Gulf Coast Challenge
Southern white rhino calf born at ZooTampa
Southfield drunk driving suspect who killed 2 women gets $1M bond
Southie native Deirdre Devlin takes home Emmy for ‘Robot Chicken’
Southington Child Porn Suspect Arraigned
Southington High's Sal Romano

Still advising your grown kids? Time to stop
Still giving marching band the college try, 35 years later
Still have damage from Irma? A new center will help those in need of hurricane repairs
Still in control, Flyers need to repeat playoff push
Still no timetable for Kristaps Porzingis' return to New York Knicks
Still want to install iOS apps with iTunes? You're in luck
Stillwater prison lockdown ends, some operations resume after officer's death
Stillwater-based Parent company of Bank SNB acquired
Sting operation busts distracted drivers caught texting behind the wheel
Sting operation recovered Dorothy's stolen ruby slippers
Sting, Robert Plant, John Mayer headline music lineup for Bourbon & Beyond Festival
Stingl:  Move over Delafield: Milwaukee has a smiley barn too, or maybe just a scared one
Stingl: Adopted son sets out to find his birth parents, who then reconnect and get married
Stingl: Grandmas are wedding flower girls. Wait till you hear where the rose petals came from.
Stingl:

Sweden Is Great at Turning Trash to Energy
Sweden Pulls The Plug On Popular, Citizen-Run Twitter Experiment
Sweden is starting to talk about leaving the EU — here's what a 'Swexit' might look like
Sweden’s Economy Is Getting a Lift From Migrants
Swedish Family Gets $2 Billion Boost From H&M Buyout Speculation
Swedish Gangster Movie 'Easy Money' At Cinestudio
Swedish Meatballs Alfredo
Swedish Pancakes
Swedish Premier Set to Lose First Round in Bid to Stay in Power
Swedish Yule Celebration A Tasty Tradition
Swedish leader voices anger after dozens of cars are burned
Swedish regulator says contraceptive app works as advertised
Sweet & Savory Pineapple Cheese Ball
Sweet & Sour Pork Wraps
Sweet & Tangy Salmon with Green Beans
Sweet 'n' Sour Ribs
Sweet 'n' Spicy Chicken
Sweet 'n' Tangy Chicken Wings | Taste of Home
Sweet Barbecued Pork Chops
Sweet Candied Carrots
Sweet Corn Muffins
Sweet Corn and Potato Gratin
Sweet Diabetic Snacks for Diabetics | Reader's Digest
Sweet Ham Steak
Sweet Heaven

Ted Ginn Makes Definitive Statement About Week 3 Status
Ted Ginn scores TD, Mark Ingram reacts
Ted Kroll Dies At 82
Ted Leonsis giving Stanley Cup rings to Monumental employees | WTOP
Ted Nugent speaks God, guns and parenting at Great America Outdoor Show
Teddy Bear Facts | Reader's Digest
Teddy Bridgewater headed to Saints after New Orleans pulls off huge trade with Jets
Teddy Bridgewater's comeback continues as Brees' back-up after trade to Saints
Teddy Bridgewater: I don't mind waiting behind Brees
Teddy Geiger Is Dating Emily Hampshire And They Look Adorable
Teddy Perkins sits front-row at the Emmys, creeps out viewers
Teddy Perkins, Donald Glover's Creepy 'Atlanta' Character, Spotted in Emmys Audience
Teen "set-up" by man he met on Grindr, beaten in ruthless attack
Teen Accused Of Killing Dad Returned To Florida
Teen Accused of Quadruple Manslaughter Pleads Not Guilty
Teen Admits Making Bomb Threats That Led To 400 Schools Being Evacuated
Teen Arrested In Tuskawilla School Fire
Te

KeyboardInterrupt: 